In [1]:
import pandas as pd
import string
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
import nltk
from nltk.stem import PorterStemmer, WordNetLemmatizer
from nltk import pos_tag
from keras.models import Sequential
from keras.layers import Embedding, LSTM, Dense
from tensorflow.keras.preprocessing.sequence import pad_sequences
import re
from keras.preprocessing.text import Tokenizer
from tensorflow.keras.utils import to_categorical
import numpy as np


In [2]:
with open('pg345.txt', 'r') as file:
    data = file.read()
print(data)

ï»¿DRACULA




CHAPTER I

JONATHAN HARKER'S JOURNAL

(_Kept in shorthand._)


_3 May. Bistritz._--Left Munich at 8:35 P. M., on 1st May, arriving at
Vienna early next morning; should have arrived at 6:46, but train was an
hour late. Buda-Pesth seems a wonderful place, from the glimpse which I
got of it from the train and the little I could walk through the
streets. I feared to go very far from the station, as we had arrived
late and would start as near the correct time as possible. The
impression I had was that we were leaving the West and entering the
East; the most western of splendid bridges over the Danube, which is
here of noble width and depth, took us among the traditions of Turkish
rule.

We left in pretty good time, and came after nightfall to Klausenburgh.
Here I stopped for the night at the Hotel Royale. I had for dinner, or
rather supper, a chicken done up some way with red pepper, which was
very good but thirsty. (_Mem._, get recipe for Mina.) I asked the
waiter, and he sa

In [3]:
data = re.sub(r'[^a-zA-Z0-9\s]', '', data)

# remove extra white space
data = re.sub(r'\s+', ' ', data)
# remove punctuation marks
data = data.translate(str.maketrans('', '', string.punctuation))

# convert text to lowercase
data = data.lower()

# remove stop words
stop_words = set(stopwords.words('english'))
words = word_tokenize(data)
filtered_words = [word for word in words if word not in stop_words]

# print tokenized text
print(filtered_words)

['dracula', 'chapter', 'jonathan', 'harkers', 'journal', 'kept', 'shorthand', '3', 'may', 'bistritzleft', 'munich', '835', 'p', '1st', 'may', 'arriving', 'vienna', 'early', 'next', 'morning', 'arrived', '646', 'train', 'hour', 'late', 'budapesth', 'seems', 'wonderful', 'place', 'glimpse', 'got', 'train', 'little', 'could', 'walk', 'streets', 'feared', 'go', 'far', 'station', 'arrived', 'late', 'would', 'start', 'near', 'correct', 'time', 'possible', 'impression', 'leaving', 'west', 'entering', 'east', 'western', 'splendid', 'bridges', 'danube', 'noble', 'width', 'depth', 'took', 'us', 'among', 'traditions', 'turkish', 'rule', 'left', 'pretty', 'good', 'time', 'came', 'nightfall', 'klausenburgh', 'stopped', 'night', 'hotel', 'royale', 'dinner', 'rather', 'supper', 'chicken', 'done', 'way', 'red', 'pepper', 'good', 'thirsty', 'mem', 'get', 'recipe', 'mina', 'asked', 'waiter', 'said', 'called', 'paprika', 'hendl', 'national', 'dish', 'able', 'get', 'anywhere', 'along', 'carpathians', 'fou

In [11]:
chars = sorted(list(set(data)))
char_to_int = dict((c, i) for i, c in enumerate(chars))

In [5]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts([data])
tokenized_text = tokenizer.texts_to_sequences([data])

In [6]:
# perform stemming
stemmer = PorterStemmer()
stemmed_words = [stemmer.stem(word) for word in filtered_words]

# perform lemmatization
lemmatizer = WordNetLemmatizer()
lemmatized_words = [lemmatizer.lemmatize(word) for word in filtered_words]

# perform part-of-speech tagging
pos_tags = pos_tag(filtered_words)

print("Filtered words:", filtered_words)
print("Stemmed words:", stemmed_words)
print("Lemmatized words:", lemmatized_words)
print("POS tags:", pos_tags)

Filtered words: ['dracula', 'chapter', 'jonathan', 'harkers', 'journal', 'kept', 'shorthand', '3', 'may', 'bistritzleft', 'munich', '835', 'p', '1st', 'may', 'arriving', 'vienna', 'early', 'next', 'morning', 'arrived', '646', 'train', 'hour', 'late', 'budapesth', 'seems', 'wonderful', 'place', 'glimpse', 'got', 'train', 'little', 'could', 'walk', 'streets', 'feared', 'go', 'far', 'station', 'arrived', 'late', 'would', 'start', 'near', 'correct', 'time', 'possible', 'impression', 'leaving', 'west', 'entering', 'east', 'western', 'splendid', 'bridges', 'danube', 'noble', 'width', 'depth', 'took', 'us', 'among', 'traditions', 'turkish', 'rule', 'left', 'pretty', 'good', 'time', 'came', 'nightfall', 'klausenburgh', 'stopped', 'night', 'hotel', 'royale', 'dinner', 'rather', 'supper', 'chicken', 'done', 'way', 'red', 'pepper', 'good', 'thirsty', 'mem', 'get', 'recipe', 'mina', 'asked', 'waiter', 'said', 'called', 'paprika', 'hendl', 'national', 'dish', 'able', 'get', 'anywhere', 'along', 'ca

In [7]:
tokenizer = Tokenizer()
sequences = tokenizer.texts_to_sequences(lemmatized_words)

In [8]:
padded_sequences = pad_sequences(sequences, maxlen=100, truncating='post')

In [9]:
X = padded_sequences[:, :-1]
y =to_categorical(padded_sequences[:, -1], num_classes=len(tokenizer.word_index)+1)

In [10]:
# define the number of words in the vocabulary
model_lemma = Sequential()
model_lemma.add(Embedding(input_dim=len(tokenizer.word_index)+1, output_dim=50, input_length= 100-1))
model_lemma.add(LSTM(100))
model_lemma.add(Dense(len(tokenizer.word_index)+1, activation='softmax'))
model_lemma.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
model_lemma.fit(X, y.reshape((73207, 1)), epochs=10, verbose=1)

Epoch 1/10
2288/2288 [==============================] - 67s 29ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 2/10
2288/2288 [==============================] - 67s 29ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 3/10
2288/2288 [==============================] - 67s 29ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 4/10
2288/2288 [==============================] - 68s 30ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 5/10
2288/2288 [==============================] - 70s 30ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 6/10
2288/2288 [==============================] - 68s 30ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 7/10
2288/2288 [==============================] - 70s 30ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 8/10
2288/2288 [==============================] - 70s 31ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 9/10
2288/2288 [==============================] - 70s 31ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 10/10
2288/2288 [=====

In [12]:
int_to_char = dict((i, c) for i, c in enumerate(chars))

In [13]:
n_vocab = len(chars)

In [ ]:
import tensorflow as tf

# Set the length of the generated text
text_length = 100

# Set the temperature for text sampling
temperature = 0.5

# Choose a random starting seed

seed = data

# Preprocess the seed text
input_text = [char_to_int[char] for char in seed]
input_text = tf.keras.preprocessing.sequence.pad_sequences([input_text], maxlen=99)

# Generate text
generated_text = seed
for i in range(text_length):
    # Predict the next character based on the current generated text
    predictions = model_lemma.predict(input_text, verbose=0)
    predictions = np.squeeze(predictions)
    
    # Sample the next character based on the predicted probabilities
    predictions = predictions / temperature
    predicted_id = tf.random.categorical(predictions, num_samples=1)[-1,0].numpy()
    
    # Convert the predicted character ID back to a character and add it to the generated text
    next_char = int_to_char[predicted_id]
    generated_text += next_char
    
    # Update the input text by removing the first character and adding the predicted character
    input_text = np.roll(input_text, -1, axis=1)
    input_text[0, -1] = predicted_id

print(generated_text)